In [61]:
import numpy as np

from sklearn.model_selection import train_test_split, GridSearchCV, PredefinedSplit
from sklearn.preprocessing import StandardScaler, MinMaxScaler
from sklearn import metrics
from sklearn.neighbors import KNeighborsClassifier
from sklearn.svm import SVC

from keras import models, Input
from keras import optimizers as opt
from keras import backend as K
from keras.layers import Dense
from keras_tuner.tuners import RandomSearch
from tensorflow.keras.utils import to_categorical

In [62]:
from dataset import load_dataset, load_labels, split_data, format_labels
from features import time_series_features, fractal_features, entropy_features, hjorth_features, freq_band_features
import variables as v

# Variables

In [63]:
data_type = "ica_filtered"
test_type = "Arithmetic"

# Load Dataset

In [64]:
dataset_ = load_dataset(data_type=data_type, test_type=test_type)
dataset = split_data(dataset_, v.SFREQ)

In [65]:
label_ = load_labels()
label = format_labels(label_, test_type=test_type, epochs=dataset.shape[1])

# Compute Features

In [66]:
# features = time_series_features(dataset)
# freq_bands = np.array([1, 4, 8, 12, 30, 50])
# features = freq_band_features(dataset, freq_bands)
# features = hjorth_features(dataset)
# features = entropy_features(dataset)
features = fractal_features(dataset)

In [67]:
data = features

# k-NN Classifier

In [68]:
x, x_test, y, y_test = train_test_split(
    data, label, test_size=0.2, random_state=1)
x_train, x_val, y_train, y_val = train_test_split(
    x, y, test_size=0.25, random_state=1)
scaler = MinMaxScaler()
scaler.fit(x_train)
x = scaler.transform(x)
x_train = scaler.transform(x_train)
x_val = scaler.transform(x_val)
x_test = scaler.transform(x_test)

param_grid = {
    'leaf_size': range(50),
    'n_neighbors': range(1, 10),
    'p': [1, 2]
}
split_index = [-1 if x in range(len(x_train)) else 0 for x in range(len(x))]
ps = PredefinedSplit(test_fold=split_index)
knn_clf = GridSearchCV(KNeighborsClassifier(), param_grid, cv=ps, refit=True)
knn_clf.fit(x, y)

In [ ]:
y_pred = knn_clf.predict(x_test)
y_true = y_test

In [ ]:
print(metrics.classification_report(y_true, y_pred))
print(metrics.confusion_matrix(y_true, y_pred))

              precision    recall  f1-score   support

       False       0.57      0.55      0.56       311
        True       0.54      0.56      0.55       289

    accuracy                           0.56       600
   macro avg       0.56      0.56      0.55       600
weighted avg       0.56      0.56      0.56       600

[[170 141]
 [126 163]]


# SVM Classifier

In [ ]:
x, x_test, y, y_test = train_test_split(
    data, label, test_size=0.2, random_state=1)
x_train, x_val, y_train, y_val = train_test_split(
    x, y, test_size=0.25, random_state=1)

param_grid = {
    'C': [0.1, 1, 10, 100, 1000],
    'kernel': ['rbf']
}
split_index = [-1 if x in range(len(x_train)) else 0 for x in range(len(x))]
ps = PredefinedSplit(test_fold=split_index)
svm_clf = GridSearchCV(SVC(), param_grid, cv=ps, refit=True)
svm_clf.fit(x, y)

GridSearchCV(cv=PredefinedSplit(test_fold=array([-1, -1, ...,  0,  0])),
             estimator=SVC(),
             param_grid={'C': [0.1, 1, 10, 100, 1000], 'kernel': ['rbf']})

In [ ]:
y_pred = svm_clf.predict(x_test)
y_true = y_test

In [ ]:
print(metrics.classification_report(y_true, y_pred))
print(metrics.confusion_matrix(y_true, y_pred))

              precision    recall  f1-score   support

       False       0.60      0.59      0.59       311
        True       0.56      0.57      0.57       289

    accuracy                           0.58       600
   macro avg       0.58      0.58      0.58       600
weighted avg       0.58      0.58      0.58       600

[[183 128]
 [124 165]]


# Multilayer Perceptron

In [ ]:
K.clear_session()
y_v = label
y_v = to_categorical(y_v)
x_train, x_test, y_train, y_test = train_test_split(
    data, y_v, test_size=0.2, random_state=1)
x_train, x_val, y_train, y_val = train_test_split(
    x_train, y_train, test_size=0.25, random_state=1)

In [ ]:
def model_builder(hp):
    model = models.Sequential()
    model.add(Input(shape=(x_train.shape[1],)))

    for i in range(hp.Int('layers', 2, 6)):
        model.add(Dense(units=hp.Int('units_' + str(i), 32, 1024, step=32),
                        activation=hp.Choice('act_' + str(i), ['relu', 'sigmoid'])))

    model.add(Dense(v.N_CLASSES, activation='softmax', name='out'))

    hp_learning_rate = hp.Choice('learning_rate', values=[1e-2, 1e-3, 1e-4])

    model.compile(optimizer=opt.adam_v2.Adam(learning_rate=hp_learning_rate),
                  loss="binary_crossentropy",
                  metrics=['accuracy'])
    return model

In [ ]:
tuner = RandomSearch(
    model_builder,
    objective='val_accuracy',
    max_trials=15,
    executions_per_trial=2,
    overwrite=True
)

In [ ]:
tuner.search(x_train, y_train, epochs=50, validation_data=[x_val, y_val])

Trial 15 Complete [00h 01m 08s]
val_accuracy: 0.5450000166893005

Best val_accuracy So Far: 0.5541666746139526
Total elapsed time: 00h 14m 40s
INFO:tensorflow:Oracle triggered exit


In [ ]:
model = tuner.get_best_models(num_models=1)[0]

In [ ]:
y_pred = model.predict(x_test)
y_true = y_test
y_pred = np.argmax(y_pred, axis=1)
y_true = np.argmax(y_true, axis=1)

2022-12-11 13:24:08.707790: I tensorflow/core/grappler/optimizers/custom_graph_optimizer_registry.cc:113] Plugin optimizer for device_type GPU is enabled.


In [ ]:
print(metrics.classification_report(y_true, y_pred))
print(metrics.confusion_matrix(y_true, y_pred))

              precision    recall  f1-score   support

           0       0.52      0.90      0.66       311
           1       0.52      0.11      0.19       289

    accuracy                           0.52       600
   macro avg       0.52      0.51      0.43       600
weighted avg       0.52      0.52      0.43       600

[[281  30]
 [256  33]]
